# Model 4: Predict Star Formation Variables (M*) Based on Visual Morphology (galaxy image)


In [1]:
#Loading needed modules and classes/functions 
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
import torch
from torch.autograd import Variable
from torch.utils.data import DataLoader
from torch.utils.data import TensorDataset
from torchvision.datasets import ImageFolder 
from torchvision.io import read_image
from torchvision.io import decode_image
import torchvision
import torchvision.transforms as transforms
import torch.nn as nn
import torch.optim as optim
import torch.nn.functional as F
import marvin
from marvin.tools.maps import Maps
from marvin.tools.image import Image
from marvin.utils.general.images import get_images_by_list
from marvin import config
from marvin.tools.cube import Cube
from sklearn import metrics
from sklearn.metrics import accuracy_score, confusion_matrix,r2_score
from sklearn.model_selection import train_test_split
import os
import shutil
from PIL import Image as image_PIL
import time 

#set config attributes and turn on global downloads of Marvin data
config.setRelease('DR15')
config.mode = 'local'
config.download = True

%matplotlib qt




[INFO]: No release version set. Setting default to DR15
[WARNING]: path /home/juanp/sas/mangawork/manga/spectro/redux/v2_4_3/drpall-v2_4_3.fits cannot be found. Setting drpall to None. (MarvinUserWarning)
[WARNING]: path /home/juanp/sas/mangawork/manga/spectro/analysis/v2_4_3/2.2.1/dapall-v2_4_3-2.2.1.fits cannot be found. Setting dapall to None. (MarvinUserWarning)
[WARNING]: path /home/juanp/sas/mangawork/manga/spectro/redux/v2_4_3/drpall-v2_4_3.fits cannot be found. Setting drpall to None. (MarvinUserWarning)
[WARNING]: path /home/juanp/sas/mangawork/manga/spectro/analysis/v2_4_3/2.2.1/dapall-v2_4_3-2.2.1.fits cannot be found. Setting dapall to None. (MarvinUserWarning)


# Importing Data from Schema Table

In [2]:


data=pd.read_csv('CompleteTable.csv')  #Importing All MaNGA Data from DPRall Schema

galaxy_list=np.loadtxt('Query Results',dtype=str) #Pulling Manga ID's of galaxies which satisfy log(M) > 9 and 0 < z < 0.1


#Problem with image associated with manga id at galaxy_list[3548], mangaid- 1-135668
galaxy_list=np.delete(galaxy_list,3548)

galaxy_list=np.unique(galaxy_list)


galaxy_index=np.zeros(len(galaxy_list)) 
for i in range (len(galaxy_list)): #Getting the index of these galaxies in the schema table
    galaxy_index[i]=np.where(data.loc[:,'mangaid']==galaxy_list[i])[0][0]

galaxy_index=np.array(galaxy_index,dtype=int) #Ensuring we have array that can be used to index, force int 

galaxies=data.iloc[galaxy_index] #DF of galaxies which satisfies the condition, contains all relevant schema data 

galaxies=galaxies.sort_values(by=['plateifu']) #Sorting galaxies by plateifu to match ImageFolder Output 

#Creating the arrays of the independent variables were are interested in, and dependent variable n 

mass=galaxies.loc[:,'nsa_sersic_mass']
log_mass=np.log10(mass)

SFR=galaxies.loc[:,'sfr_tot']
log_SFR=np.log10(SFR)

ha_flux=galaxies.loc[:,'emline_gflux_tot_ha_6564']

mangaid=galaxies.loc[:,'mangaid']
plateifu=galaxies.loc[:,'plateifu']

if plateifu.all()==np.unique(plateifu).all() and mangaid.all()==np.unique(mangaid.all()):
    print('Is Unique List of Galaxies')
    
else:
    print('Try Again')

n=galaxies.loc[:,'nsa_sersic_n']
n=np.array(n,dtype=np.float32)
n=torch.from_numpy(n).to('cuda:0').reshape(-1,1)


Is Unique List of Galaxies


# Importing Images from their Downloaded Locations 


In [3]:
# function to resize image
def resize_image(src_image, size=(128,128), bg_color="white"): 
    from PIL import Image, ImageOps 
    
    # resize the image so the longest dimension matches our target size
    src_image.thumbnail(size, Image.ANTIALIAS)
    
    # Create a new square background image
    new_image = Image.new("RGB", size, bg_color)
    
    # Paste the resized image into the center of the square background
    new_image.paste(src_image, (int((size[0] - src_image.size[0]) / 2), int((size[1] - src_image.size[1]) / 2)))
  
    # return the resized image
    return new_image


# Putting the Images into DataLoaders

In [4]:
img_size=(128,128)

# image=ImageFolder('/home/juanp/sas/dr15/manga/spectro/redux/v2_4_3/') #Picks up 3590 pictures, directory list has lenght 3637 however 

# torch.manual_seed(15)
# np.random.seed(15)


image_directory='/home/juanp/sas/dr15/manga/spectro/redux/v2_4_3'
classes= sorted(os.listdir(image_directory))

batch_size=50
image_copies=30

def load_dataset(data_path):
    # Load all the images
    transformation = transforms.Compose([
        # Randomly augment the image data
            # Random horizontal flip
        transforms.RandomHorizontalFlip(0.5),
            # Random vertical flip
        transforms.RandomVerticalFlip(0.3),
        #Rotates the image by some angle
        transforms.RandomRotation(0,360),
        # transform to tensors
        transforms.ToTensor(),
        # Normalize the pixel values (in R, G, and B channels)
        # transforms.Normalize(mean=[0.5, 0.5, 0.5], std=[0.5, 0.5, 0.5])
    ])

    # Load all of the images, transforming them
    full_dataset = torchvision.datasets.ImageFolder(
        root=data_path,
        # transform=transformation
    )
    
    #This loop transforms the images and assigns them the correct label 

    full_dataset_v2 = []   
    for i in range(len(full_dataset)): 
        for j in range(image_copies): #This loops makes it so we have 5 copies of each galaxy image with different orientations 
            temp=transformation(resize_image(full_dataset[i][0]))
            full_dataset_v2.append((temp,log_mass.iloc[i])) 
    
    full_dataset=full_dataset_v2

    print(len(full_dataset))


    # Split into training (70% and testing (30%) datasets)
    train_size = int(0.7 * len(full_dataset))
    test_size = len(full_dataset) - train_size
    
    # use torch.utils.data.random_split for training/test split
    train_dataset, test_dataset = torch.utils.data.random_split(full_dataset, [train_size, test_size])
    
    # define a loader for the training data we can iterate through in 50-image batches
    train_loader = torch.utils.data.DataLoader(
        train_dataset,
        batch_size=batch_size,
        num_workers=0,
        shuffle=False
    )
    
    # define a loader for the testing data we can iterate through in 50-image batches
    test_loader = torch.utils.data.DataLoader(
        test_dataset,
        batch_size=batch_size,
        num_workers=0,
        shuffle=False
    )
        
    return train_loader, test_loader




#####################################################################################################



# Get the iterative dataloaders for test and training data
train_loader, test_loader = load_dataset(image_directory)
batch_size = train_loader.batch_size
print("Data loaders ready to read", image_directory)



107670
Data loaders ready to read /home/juanp/sas/dr15/manga/spectro/redux/v2_4_3


# Defining the Model 

In [5]:
# Create a neural net class
class Net(nn.Module):
    
    
    # Defining the Constructor
    def __init__(self, num_classes=3):
        super(Net, self).__init__()
        
        # In the init function, we define each layer we will use in our model
        
        # Our images are RGB, so we have input channels = 3. 
        # We will apply 12 filters in the first convolutional layer
        self.conv1 = nn.Conv2d(in_channels=3, out_channels=12, kernel_size=3, stride=1, padding=1)
        
        # A second convolutional layer takes 12 input channels, and generates 24 outputs
        self.conv2 = nn.Conv2d(in_channels=12, out_channels=24, kernel_size=3, stride=1, padding=1)
        
        # We in the end apply max pooling with a kernel size of 2
        self.pool = nn.MaxPool2d(kernel_size=2)
        
        # A drop layer deletes 20% of the features to help prevent overfitting
        self.drop = nn.Dropout2d(p=0.2)
        
        # Our 128x128 image tensors will be pooled twice with a kernel size of 2. 128/2/2 is 32.
        # This means that our feature tensors are now 128 x 128, and we've generated 24 of them
        
        # We need to flatten these in order to feed them to a fully-connected layer
        self.fc = nn.Linear(in_features=32 * 32 * 24, out_features=10)

        self.fc1= nn.Linear(in_features=10, out_features=1)


    def forward(self, x):
        # x=x+1
        
        # In the forward function, pass the data through the layers we defined in the init function
        # print(x)
        # Use a ReLU activation function after layer 1 (convolution 1 and pool)
        x=self.conv1(x)
        
        x=self.pool(x)
       

        x=F.relu(x)

        
      
 
     
        # Use a ReLU activation function after layer 2
        x = F.relu(self.pool(self.conv2(x))) 
        
        
        # Select some features to drop to prevent overfitting (only drop during training)
        x = F.dropout(self.drop(x), training=self.training)
        
        # Flatten
        x = x.view(-1, 32 * 32 * 24)
        # Feed to fully-connected layer to predict class
        x = self.fc(x)
        
        # Return class probabilities via a log_softmax function
        x=F.relu(x) 
        
        x= self.fc1(x)
        # print(x)
        return x
    
device = "cpu"
if (torch.cuda.is_available()):
    # if GPU available, use cuda (on a cpu, training will take a considerable length of time!)
    device = "cuda"

# Create an instance of the model class and allocate it to the device
model = Net(num_classes=len(SFR)).to('cuda')

print(model)

Net(
  (conv1): Conv2d(3, 12, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
  (conv2): Conv2d(12, 24, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
  (pool): MaxPool2d(kernel_size=2, stride=2, padding=0, dilation=1, ceil_mode=False)
  (drop): Dropout2d(p=0.2, inplace=False)
  (fc): Linear(in_features=24576, out_features=10, bias=True)
  (fc1): Linear(in_features=10, out_features=1, bias=True)
)


# Creating Training Loop/Function

In [6]:
def train(model, device, train_loader, optimizer, epoch):
    # Set the model to training mode
    model.train()
    train_loss = 0
    # print("Epoch:", epoch)
    # Process the images in batches
    for batch_idx, (data, target) in enumerate(train_loader):

        target=target.float()
        # print(target.shape)
        target=target.reshape(-1,1)
        # Use the CPU or GPU as appropriate
        # Recall that GPU is optimized for the operations we are dealing with
        data, target = data.to(device), target.to(device)
        
        # Reset the optimizer
        optimizer.zero_grad()
        
        # Push the data forward through the model layers
    
        output = model(data)

        
        # Get the loss
        loss = loss_criteria(output, target)
        if batch_idx==0:
            print(output,target,output-target,loss)
        # Keep a running total
        train_loss += loss.item()
        
        # Backpropagate
        loss.backward()
        optimizer.step()

       
        
        # Print metrics so we see some progress
        # print('\tTraining batch {} Loss: {:.6f}'.format(batch_idx + 1, loss.item()))
            
    # return average loss for the epoch
    avg_loss = train_loss / (batch_idx+1)
    # print('Training set: Average loss: {:.6f}'.format(avg_loss))
    return avg_loss

# Create Test Function

In [7]:
def test(model, device, test_loader):
    # Switch the model to evaluation mode (so we don't backpropagate or drop)
    model.eval()
    test_loss = 0
    correct = 0
    with torch.no_grad():
        batch_count = 0
        for data, target in test_loader:
            target=target.float()
            target=target.reshape(-1,1)
            batch_count += 1
            data, target = data.to(device), target.to(device)
            
            # Get the predicted classes for this batch
            output = model(data)
            
            # Calculate the loss for this batch
            test_loss += loss_criteria(output, target).item()
            
            # Calculate the accuracy for this batch
            _, predicted = torch.max(output.data, 1)
            correct += torch.sum(target==predicted).item()

    # Calculate the average loss and total accuracy for this epoch
    avg_loss = test_loss / batch_count
    # print('Validation set: Average loss: {:.6f}, Accuracy: {}/{} ({:.0f}%)\n'.format(
    #     avg_loss, correct, len(test_loader.dataset),
    #     100. * correct / len(test_loader.dataset)))
    
    # return average loss for the epoch
    return avg_loss

# Training the Model

In [8]:
# Use an "Adam" optimizer to adjust weights
optimizer = optim.Adam(model.parameters(), lr=0.001)

# Specify the loss criteria
loss_criteria = nn.MSELoss(reduction='sum')

# Track metrics in these arrays
epoch_nums = []
training_loss = []
validation_loss = []


# Train over 10 epochs (We restrict to 10 for time issues)
epochs = 1000
print('Training on', device)
time_start = time.time()
for epoch in range(1, epochs + 1):
        print(epoch)
        train_loss = train(model, device, train_loader, optimizer, epoch)
        test_loss = test(model, device, test_loader)
        epoch_nums.append(epoch)
        training_loss.append(train_loss)
        validation_loss.append(test_loss)
torch.save(model.state_dict(),'/home/juanp/Documents/SURP-2021/Models/Model 4 (Stellar Mass)/Mass_30Copies+Rotation')
time_end = time.time()
total_time = (time_end-time_start)/60 
print(total_time)

Training on cuda
1
tensor([[-0.0732],
        [-0.0592],
        [-0.0744],
        [-0.0767],
        [-0.0853],
        [-0.0664],
        [-0.0665],
        [-0.0607],
        [-0.0574],
        [-0.0811],
        [-0.0771],
        [-0.0656],
        [-0.0672],
        [-0.0629],
        [-0.0596],
        [-0.0760],
        [-0.0747],
        [-0.0599],
        [-0.0813],
        [-0.0698],
        [-0.0770],
        [-0.0689],
        [-0.0692],
        [-0.0660],
        [-0.0833],
        [-0.0704],
        [-0.0385],
        [-0.0569],
        [-0.0576],
        [-0.0570],
        [-0.0577],
        [-0.0637],
        [-0.0617],
        [-0.0776],
        [-0.0640],
        [-0.0737],
        [-0.0535],
        [-0.0389],
        [-0.0762],
        [-0.0558],
        [-0.0650],
        [-0.0411],
        [-0.0605],
        [-0.0519],
        [-0.0843],
        [-0.0607],
        [-0.0799],
        [-0.0326],
        [-0.0529],
        [-0.0657]], device='cuda:0', grad_fn=<Addm

4
tensor([[ 7.6164],
        [ 9.0020],
        [10.9265],
        [ 9.5530],
        [11.6535],
        [10.7363],
        [ 9.9995],
        [10.9754],
        [ 8.1115],
        [ 9.3395],
        [ 9.5163],
        [ 9.8396],
        [ 9.0253],
        [ 9.7470],
        [ 8.5045],
        [11.5129],
        [11.5707],
        [11.2074],
        [ 8.1439],
        [ 7.6095],
        [10.4745],
        [12.0491],
        [ 6.6922],
        [12.4578],
        [ 8.0648],
        [10.2955],
        [10.3375],
        [11.9508],
        [ 9.7197],
        [11.3288],
        [11.2503],
        [11.2619],
        [ 9.7285],
        [10.1962],
        [10.2283],
        [10.4074],
        [11.3826],
        [11.4287],
        [11.9604],
        [ 9.9650],
        [ 8.3952],
        [ 7.9185],
        [ 8.1986],
        [11.6744],
        [11.1944],
        [10.9347],
        [ 9.3025],
        [10.0922],
        [ 9.8088],
        [10.9717]], device='cuda:0', grad_fn=<AddmmBackward>) tenso

7
tensor([[ 9.7456],
        [ 9.8646],
        [ 9.9470],
        [10.7240],
        [ 9.7926],
        [10.0208],
        [10.4850],
        [ 9.3166],
        [ 9.7153],
        [ 9.1250],
        [10.1604],
        [ 9.8844],
        [ 9.4707],
        [ 9.1242],
        [ 9.7714],
        [10.8635],
        [ 9.6088],
        [11.2289],
        [ 9.5448],
        [ 8.4662],
        [ 9.8571],
        [10.8831],
        [ 9.8538],
        [10.8783],
        [ 9.4016],
        [10.7260],
        [10.6337],
        [11.5315],
        [ 9.3522],
        [10.1264],
        [11.0617],
        [10.4743],
        [10.5448],
        [10.0259],
        [10.5177],
        [11.1933],
        [10.2611],
        [10.0052],
        [11.1015],
        [ 9.9833],
        [ 9.1716],
        [ 9.6088],
        [ 9.3837],
        [10.5568],
        [10.9723],
        [10.4685],
        [ 9.8301],
        [10.7868],
        [10.0882],
        [ 9.5842]], device='cuda:0', grad_fn=<AddmmBackward>) tenso

10
tensor([[ 9.8539],
        [ 9.9325],
        [10.3213],
        [10.7065],
        [10.9837],
        [ 9.6889],
        [10.6520],
        [10.0375],
        [ 9.4293],
        [ 9.3980],
        [10.0694],
        [10.0560],
        [ 9.6297],
        [ 9.4973],
        [ 9.5636],
        [10.7369],
        [10.4715],
        [10.7784],
        [ 9.6760],
        [ 9.5424],
        [ 9.7337],
        [10.7133],
        [ 9.5038],
        [10.7348],
        [ 9.0092],
        [10.7115],
        [10.6685],
        [10.7666],
        [ 9.2358],
        [ 9.9118],
        [10.7255],
        [ 9.4642],
        [10.2950],
        [ 9.8924],
        [10.6683],
        [10.6432],
        [10.2216],
        [10.1715],
        [11.0766],
        [ 9.6126],
        [ 9.7887],
        [ 9.9312],
        [ 9.4781],
        [10.6821],
        [10.2478],
        [10.2154],
        [11.1313],
        [10.2890],
        [10.0969],
        [ 9.8392]], device='cuda:0', grad_fn=<AddmmBackward>) tens

13
tensor([[ 9.7947],
        [ 9.8566],
        [10.6076],
        [11.1391],
        [10.8567],
        [ 9.6973],
        [11.2148],
        [10.1234],
        [ 9.0239],
        [ 9.3251],
        [10.1717],
        [ 9.9988],
        [ 9.4844],
        [ 9.0067],
        [ 9.6187],
        [10.7122],
        [10.5305],
        [10.5978],
        [ 9.5729],
        [ 9.9187],
        [ 9.8357],
        [11.1201],
        [ 9.1645],
        [10.7659],
        [ 9.1584],
        [10.8432],
        [11.0037],
        [11.3785],
        [ 9.2604],
        [10.0502],
        [10.6744],
        [ 9.2795],
        [10.3400],
        [ 9.6336],
        [10.9540],
        [10.5785],
        [10.2519],
        [10.2571],
        [11.1069],
        [ 9.4918],
        [ 9.8544],
        [10.0152],
        [ 9.1432],
        [11.1615],
        [10.4834],
        [10.0475],
        [10.8638],
        [10.4393],
        [10.0563],
        [ 9.9951]], device='cuda:0', grad_fn=<AddmmBackward>) tens

...

988
tensor([[ 9.6376],
        [10.0989],
        [10.2279],
        [10.8648],
        [11.0009],
        [ 9.5499],
        [10.8127],
        [ 9.9376],
        [ 9.0885],
        [ 9.2442],
        [ 9.7547],
        [10.4680],
        [ 9.7643],
        [ 9.2003],
        [ 9.5059],
        [10.6205],
        [10.1347],
        [10.6580],
        [ 9.4678],
        [ 9.4364],
        [ 9.7678],
        [10.9840],
        [ 9.4420],
        [10.8274],
        [ 9.1121],
        [10.9185],
        [10.8060],
        [11.3213],
        [ 9.3387],
        [ 9.8724],
        [10.8906],
        [ 9.2735],
        [10.6502],
        [ 9.6631],
        [10.8397],
        [10.8543],
        [10.1333],
        [10.3019],
        [11.0723],
        [ 9.6687],
        [ 9.7115],
        [10.5087],
        [ 9.3763],
        [11.2649],
        [10.2932],
        [ 9.9409],
        [10.9220],
        [10.2951],
        [10.4207],
        [ 9.9888]], device='cuda:0', grad_fn=<AddmmBackward>) ten

991
tensor([[ 9.6036],
        [ 9.9605],
        [10.0934],
        [10.3326],
        [10.7720],
        [ 9.6008],
        [10.9201],
        [ 9.8709],
        [ 9.3390],
        [ 9.3919],
        [ 9.7648],
        [10.0799],
        [ 9.8882],
        [ 9.1410],
        [ 9.3433],
        [10.9171],
        [10.3320],
        [10.3535],
        [ 9.4034],
        [ 9.5002],
        [ 9.7982],
        [11.2487],
        [ 9.3356],
        [10.8330],
        [ 9.3041],
        [10.7215],
        [10.7244],
        [11.3517],
        [ 9.2616],
        [ 9.7542],
        [10.6764],
        [ 9.1248],
        [10.5923],
        [ 9.4910],
        [10.8903],
        [10.5680],
        [10.2841],
        [10.5205],
        [10.9478],
        [ 9.6600],
        [ 9.5130],
        [10.2916],
        [ 9.4176],
        [11.1697],
        [10.0318],
        [ 9.7277],
        [10.8506],
        [10.5739],
        [10.1935],
        [ 9.9367]], device='cuda:0', grad_fn=<AddmmBackward>) ten

994
tensor([[ 9.5886],
        [10.0190],
        [10.1503],
        [10.7082],
        [11.1710],
        [ 9.4818],
        [10.8716],
        [10.1365],
        [ 9.2903],
        [ 9.3175],
        [10.1124],
        [10.1753],
        [ 9.8957],
        [ 9.1020],
        [ 9.3517],
        [10.6862],
        [10.2050],
        [10.6113],
        [ 9.3951],
        [ 9.3453],
        [ 9.6783],
        [11.1901],
        [ 9.2613],
        [10.8724],
        [ 9.0353],
        [11.1111],
        [10.7847],
        [10.9901],
        [ 9.2282],
        [10.0148],
        [10.7039],
        [ 9.2400],
        [10.9075],
        [ 9.5683],
        [10.9298],
        [10.8269],
        [10.2899],
        [10.3168],
        [11.1961],
        [ 9.5655],
        [ 9.6747],
        [10.2497],
        [ 9.2606],
        [10.9408],
        [10.0569],
        [ 9.3862],
        [10.8565],
        [10.3748],
        [10.3425],
        [ 9.5773]], device='cuda:0', grad_fn=<AddmmBackward>) ten

997
tensor([[ 9.5433],
        [ 9.9927],
        [10.4527],
        [10.8557],
        [10.9247],
        [ 9.6174],
        [10.9588],
        [ 9.9356],
        [ 9.3284],
        [ 9.2672],
        [ 9.9066],
        [10.4498],
        [ 9.7973],
        [ 9.1862],
        [ 9.2574],
        [10.9163],
        [10.4494],
        [10.4767],
        [ 9.4360],
        [ 9.4771],
        [ 9.7451],
        [11.0818],
        [ 9.2948],
        [10.8308],
        [ 9.2065],
        [10.7871],
        [10.6407],
        [11.1661],
        [ 9.3794],
        [ 9.7535],
        [10.8051],
        [ 9.4176],
        [10.4952],
        [ 9.6835],
        [10.7060],
        [11.2196],
        [ 9.9833],
        [10.2532],
        [11.0169],
        [ 9.5259],
        [ 9.7874],
        [10.5588],
        [ 9.5156],
        [11.5432],
        [ 9.9871],
        [ 9.8848],
        [10.8330],
        [10.3848],
        [10.2175],
        [ 9.8876]], device='cuda:0', grad_fn=<AddmmBackward>) ten

1000
tensor([[ 9.6087],
        [10.1275],
        [10.3045],
        [10.6862],
        [10.9559],
        [ 9.3641],
        [11.1213],
        [ 9.8124],
        [ 9.2616],
        [ 9.4157],
        [ 9.8620],
        [10.4758],
        [ 9.9555],
        [ 9.1171],
        [ 9.5320],
        [11.0637],
        [10.3235],
        [10.5527],
        [ 9.3820],
        [ 9.6579],
        [ 9.8179],
        [11.1615],
        [ 9.4910],
        [10.9122],
        [ 9.3987],
        [10.8239],
        [10.9256],
        [11.3644],
        [ 9.2245],
        [ 9.6914],
        [10.8264],
        [ 9.2693],
        [11.0481],
        [ 9.5914],
        [10.8728],
        [11.1005],
        [10.3734],
        [10.4252],
        [11.2602],
        [ 9.5736],
        [ 9.8976],
        [10.2275],
        [ 9.3445],
        [11.1301],
        [10.2256],
        [ 9.7915],
        [10.9647],
        [10.2681],
        [10.2104],
        [ 9.8530]], device='cuda:0', grad_fn=<AddmmBackward>) te

# Checking How Well the Model is Preforming 

In [9]:
all_truths_train = [] 
all_preds_train = [] 
for (data,target) in train_loader:
    data, target = data.to(device), target.to(device)
    output=model(data)
    all_truths_train.append(target.cpu().detach().numpy())
    all_preds_train.append(output.cpu().detach().numpy()) 


incomplete_batch_id_train=len(all_truths_train)-1

remainder_train=len(all_truths_train[incomplete_batch_id_train])

total_values_train=(len(all_truths_train)*batch_size)-(batch_size-remainder_train)



all_truths_train_array=np.zeros(total_values_train)
all_preds_train_array=np.zeros(total_values_train)
k=0
while k < total_values_train:
    for i in range(len(all_truths_train)):
        if i<incomplete_batch_id_train:
            for j in range(batch_size):
                all_truths_train_array[k]=all_truths_train[i][j]
                all_preds_train_array[k]=all_preds_train[i][j]
                k=k+1
                


        else:
            i=incomplete_batch_id_train
            for j in range(remainder_train):
                all_truths_train_array[k]=all_truths_train[i][j]
                all_preds_train_array[k]=all_preds_train[i][j]
                k=k+1
                



# all_truths_train=all_truths_train_array
# all_preds_train=all_preds_train_array


In [10]:
all_truths_test = [] 
all_preds_test = [] 
for (data,target) in test_loader:
    data, target = data.to(device), target.to(device)
    output=model(data)
    all_truths_test.append(target.cpu().detach().numpy())
    all_preds_test.append(output.cpu().detach().numpy()) 


incomplete_batch_id_test=len(all_truths_test)-1

remainder_test=len(all_truths_test[incomplete_batch_id_test])


total_values_test=(len(all_truths_test)*batch_size)-(batch_size-remainder_test)



all_truths_test_array=np.zeros(total_values_test)
all_preds_test_array=np.zeros(total_values_test)
k=0
while k < total_values_test:
    for i in range(len(all_truths_test)):
        if i<incomplete_batch_id_test:
            for j in range(batch_size):
                all_truths_test_array[k]=all_truths_test[i][j]
                all_preds_test_array[k]=all_preds_test[i][j]
                # print(i,j,k)
                k=k+1
                
                


        else:
            i=incomplete_batch_id_test
            for j in range(remainder_test):
                all_truths_test_array[k]=all_truths_test[i][j]
                all_preds_test_array[k]=all_preds_test[i][j]
                # print(i,j,k)
                k=k+1
                
                

print(all_truths_test[3][43])
print(all_preds_test[3][43])
print(all_truths_test_array[193])
print(all_preds_test_array[193])
# all_truths_test=all_truths_test_array
# all_preds_test=all_preds_test_array



9.346294282041345
[9.454293]
9.346294282041345
9.454293251037598


In [16]:
def MSE(pred,truth,n):
    return((1/n)*np.sum((pred-truth)**2))
MSE_train=MSE(all_preds_train_array,all_truths_train_array,len(all_preds_train_array))
MSE_test=MSE(all_preds_test_array,all_truths_test_array,len(all_truths_test_array))

In [18]:
r2_train=r2_score(all_truths_train_array,all_preds_train_array)
r2_test=r2_score(all_truths_test_array,all_preds_test_array)
plt.figure(figsize=(16,12))
plt.subplot(1,2,1) 
plt.title('Test Data Set')
plt.scatter(all_truths_test_array, all_preds_test_array,color = 'b', alpha = 0.1*7/3)
plt.xlabel('Test True Values')
plt.ylabel('Test Predicted Value')
plt.text(12,8.5,'R$^2$='+ str(round(r2_test,4)))
plt.text(12,9,'MSE='+str(round(MSE_test,4)))
plt.plot([8,13],[8,13],'r--')

plt.subplot(1,2,2)
plt.title('Train Data Set')
plt.scatter(all_truths_train_array, all_preds_train_array,color = 'k', alpha = 0.1)
plt.xlabel('Train True Values')
plt.ylabel('Train Predicted Value')
plt.plot([8,13],[8,13],'r--') 
plt.text(12,8.5,'R$^2$='+str(round(r2_train,3)))
plt.text(12,9,'MSE='+str(round(MSE_train,4)))
plt.show()
plt.savefig('/home/juanp/Documents/SURP-2021/Plots/Model 4/Rotations 30 Copies of Images.png')